# Language Identification based on deep neural networks and ngrams
This approach of language identification follows the paper: Language Identification a Neural Network Approach, https://core.ac.uk/download/pdf/62918899.pdf

Feature extraction is partly inspired by:
https://github.com/conorosully/medium-articles/blob/master/src/language_classification.ipynb

## Dataset
The data can be downloaded from: https://downloads.tatoeba.org/exports/

In [19]:
# imports

import pandas as pd
from torch.utils.data import Dataset
from sklearn.feature_extraction.text import CountVectorizer
import torch
import numpy as np

In [54]:
# Set parameters

FILES = {'SENTENCES': 'sentences.csv'}
TEST_SIZE = 0.2
MIN_LENGTH = 20
MAX_LENGTH = 200
N_SAMPLES = 5000

In [55]:
# Define helper functions

# get most frequent ngrams for a specific language
def _get_ngrams(corpus, n, max_features):
    vectorizer = CountVectorizer(analyzer='char',
                                ngram_range=(n, n),
                                max_features=max_features)
    
    X = vectorizer.fit_transform(corpus)
    
    feature_names = vectorizer.get_feature_names()
    return X, feature_names

# get set of most frequent ngrams for every language
def _get_vocab(data, n, max_features, lang):
    
    vocab = set()
        
    # get ngrams for every language
    for l in lang:
        corpus = data[data.lang==l]['text']
        _, ngrams = _get_ngrams(corpus, n, max_features)
        vocab.update(ngrams)
    
    return vocab

# Find the index of a language
def _langToIndex(l, lang):
    return int(lang.index(l))

def _lineToTensor(line, lang):
    tensor = torch.zeros(len(line))
    for li, l in enumerate(line):
        tensor[li] = _langToIndex(l, lang)
        tensor = tensor.long()
    return tensor

In [56]:
# Setup dataset generates a dataset fromm the specified csv_file and parameters
# The dataset consists of a normalized frequency count of occurences of ngrams
def _setup_datasets(csv_file, ngrams=3, lang=['deu', 'eng', 'fra'], max_features=40, vocab=None):
    data_frame = pd.read_csv(csv_file,
              sep='\t',
              encoding='utf8',
              index_col=0,
              names=['lang', 'text'])

    # Filter text by length
    filter_len = [True if MIN_LENGTH <= len(t) <= MAX_LENGTH else False for t in data_frame['text']]
    data_frame = data_frame[filter_len]

    # Filter text by language
    filter_lang = [True if l in lang else False for l in data_frame['lang']]
    data_frame = data_frame[filter_lang]
    
    # Sample data per language
    data_trim = pd.DataFrame(columns=['lang', 'text'])
    
    for l in lang:
        lang_trim = data_frame[data_frame['lang']==l].sample(N_SAMPLES, random_state = 100)
        data_trim = data_trim.append(lang_trim)
        
    data_shuffle = data_trim.sample(frac=1)
    

    # Setup vocab from ngrams
    if vocab is None:
        vocab = _get_vocab(data_shuffle, ngrams, max_features, lang)

    # Get data based on vocab
    vectorizer = CountVectorizer(analyzer='char',
                        ngram_range=(ngrams, ngrams),
                        vocabulary=vocab)

    X = vectorizer.transform(data_shuffle['text'])

    feature_names = vectorizer.get_feature_names()

    features = pd.DataFrame(data=X.toarray(), columns=feature_names)

    # Normalize matrix
    count_min = features.min()
    count_max = features.max()

    features = (features - count_min) / (count_max - count_min)

    # Add labels to data
    features['lang'] = list(data_shuffle['lang'])

    # Split into train and test data
    offset = int(TEST_SIZE * features.shape[0])
    test_df = features[:offset]
    train_df = features[offset:]

    test_labels = _lineToTensor(test_df['lang'], lang)
    train_labels = _lineToTensor(train_df['lang'], lang)
    
    test_df = test_df.drop('lang', axis=1)
    train_df = train_df.drop('lang', axis=1)

    test_data = torch.tensor(test_df.values.astype(np.float32))
    train_data = torch.tensor(train_df.values.astype(np.float32))

    return (LanguageIdentificationDataset(train_data, train_labels, vocab, lang),
           LanguageIdentificationDataset(test_data, test_labels, vocab, lang))

In [57]:
# Define Dataset for Language Identification

class LanguageIdentificationDataset(Dataset):
    """Dataset with text in various languages"""
    
    def __init__(self, data, labels, vocab, lang):
        """
        Args:
            csv_file (string): Path to the csv file with annotations.
            root_dir (string): Directory with all the images.
            transform (callable, optional): Optional transform to be applied
                on a sample.
        """
        
        self._data = data
        self._labels = labels
        self._vocab = vocab
        self._lang = lang
        
    def __len__(self):
        return len(self._data)
    
    def __getitem__(self, i):
        return self._data[i], self._labels[i]
    
    def __iter__(self):
        for x in self._data:
            yield x
            
    def get_labels(self):
        return self._labels
    
    def get_vocab(self):
        return self._vocab
    
    def get_lang(self):
        return self._lang

In [58]:
# Generate specific datasets

# The sentences dataset consists of sentences in different languages
def Sentences():
    """ Defines a dataset with sentences in various languages

    Separately returns the training and test dataset

    Examples:
        >>> train_dataset, test_dataset = Sentences(ngrams=3, lang=['deu', 'eng', 'fra'])
    """
    return _setup_datasets(FILES['SENTENCES'])

In [59]:
dataset_train, dataset_test = Sentences()

In [60]:
len(dataset_train.get_vocab())
train_loader = torch.utils.data.DataLoader(dataset_train, batch_size=4, shuffle=True)
print(dataset_train)
print(train_loader)
for data in train_loader:
    inputs, labels = data
    print(f"inputs: {inputs}\n")
    print(f"labels: {labels}\n")
    

inputs: tensor([[0.0000, 0.0000, 0.3333, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.2500, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.1250, 0.0000, 0.0000, 0.3333, 0.2500, 0.0000,
         0.0000, 0.0000, 0.0000, 0.2500, 0.3333, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.3333, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.1667, 0.0000,
         0.0000, 0.2500, 0.1429, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.3333, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.2000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.2500, 0.0000, 0.0000, 0.0000, 0.5000, 0.0000, 0.0000, 0.2500],
        [0.0000, 0.0000, 0.

inputs: tensor([[0.0000, 0.0000, 0.3333, 0.0000, 0.0000, 0.0000, 0.0000, 0.3333, 0.0000,
         0.0000, 0.0000, 0.2500, 0.0000, 0.0000, 0.0000, 0.2500, 0.3333, 0.0000,
         0.0000, 0.0000, 0.0000, 0.1250, 0.2500, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.5000, 0.0000, 0.3333, 0.0000, 0.0000, 0.0000, 0.3333,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.2500,
         0.0000, 0.0000, 0.2500, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.2500, 0.1429, 0.0000, 0.2500, 0.3333, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.5000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.3333, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.5000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.2500, 0.0000, 0.0000, 0.3333, 0.5000, 0.0000, 0.0000, 0.0000],
        [0.3333, 0.0000, 0.

labels: tensor([2, 1, 2, 1])

inputs: tensor([[0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.2500, 0.0000, 0.0000,
         0.2500, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.3333, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.2500, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.2000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.2500, 0.2500, 0.0000, 0.2500,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000

inputs: tensor([[0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.5000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.3333, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.3333, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.2500, 0.0000, 0.2000, 0.0000, 0.2500, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.1667, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.3333, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.3333, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.2500, 0.0000, 0.0000, 0.0000, 0.2500,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000],
        [0.0000, 0.0000, 0.

inputs: tensor([[0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.2500, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.2000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.2500, 0.2500, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000],
        [0.0000, 0.0000, 0.

...

inputs: tensor([[0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.3333, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.2500, 0.5000, 0.0000, 0.0000, 0.2500, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.3333, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.2500,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.5000, 0.0000, 0.0000, 0.2500, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.3333, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.2500, 0.0000,
         0.0000, 0.0000, 0.3333, 0.0000, 0.3333, 0.0000, 0.0000, 0.0000, 0.0000,
         0.4000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.2500, 0.0000,
         0.5000, 0.0000, 0.0000, 0.3333, 0.5000, 0.0000, 0.0000, 0.2500],
        [0.0000, 0.0000, 0.

inputs: tensor([[0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.2500, 0.0000, 0.0000, 0.2500, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.3333, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.2500, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.3333, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.2500],
        [0.0000, 0.0000, 0.

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



inputs: tensor([[0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.2500, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.2500, 0.2500, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000],
        [0.0000, 0.0000, 0.

inputs: tensor([[0.0000, 0.3333, 0.0000, 0.3333, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.3333, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.1250, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.2500, 0.0000, 0.0000, 0.2500, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.3333, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.2500, 0.0000,
         0.2500, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000, 0.1429, 0.5000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000],
        [0.0000, 0.0000, 0.

# Modelling

In [61]:
# imports
import torch
import torch.nn as nn
import torch.nn.functional as F
import numpy as np

In [62]:
# number of ngrams corresponds to the number of cols in the feature matrix minus 1 for the target variable
DIM_INPUT = len(dataset_train.get_vocab())
DIM_OUTPUT = len(dataset_train.get_lang())

N_EPOCHS = 30
L_RATE = 0.001

In [63]:
class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()
        self.fc1 = nn.Linear(DIM_INPUT, DIM_INPUT)
        self.fc2 = nn.Linear(DIM_INPUT, DIM_INPUT)
        self.fc3 = nn.Linear(DIM_INPUT, DIM_OUTPUT)
        
    def forward(self, x):
        x = F.sigmoid(self.fc1(x))
        x = F.sigmoid(self.fc2(x))
        x = F.softmax(self.fc3(x))
        return x

In [64]:
def train(model, dataset_train, optimizer, criterion):
    # Train the model
    train_loss = 0
    train_acc = 0
    
    data = torch.utils.data.DataLoader(dataset_train, batch_size=4, shuffle=True)
    for i, (inp, lab) in enumerate(data):
        optimizer.zero_grad()
        pred = model(inp)
        loss = criterion(pred, lab)
        train_loss += loss.item()
        loss.backward()
        optimizer.step()
        train_acc += (pred.argmax(1) == lab).sum().item()

    return train_loss / len(dataset_train), train_acc / len(dataset_train)

In [68]:
def test(model, dataset_val, criterion):
    val_loss = 0
    val_acc = 0
    
    data = torch.utils.data.DataLoader(dataset_val, batch_size=4, shuffle=True)
    
    for i, (inp, lab) in enumerate(data):
        with torch.no_grad():
            pred = model(inp)
            loss = criterion(pred, lab)
            val_loss += loss.item()
            val_acc += (pred.argmax(1) == lab).sum().item()

    return val_loss / len(dataset_val), val_acc / len(dataset_val)

# Training

In [66]:
import time
from torch.utils.data.dataset import random_split

In [69]:
net = Net()
optimizer = torch.optim.Adam(net.parameters(), lr=0.001)
criterion = nn.CrossEntropyLoss()
#scheduler = torch.optim.lr_scheduler.StepLR(optimizer, 1, gamma=0.9)

train_len = int(len(dataset_train) * 0.95)
sub_train_, sub_valid_ = random_split(dataset_train, [train_len, len(dataset_train)-train_len])

for epoch in range(N_EPOCHS):
    
    start_time = time.time()
    train_loss, train_acc = train(net, sub_train_, optimizer, criterion)
    valid_loss, valid_acc = test(net, sub_valid_, criterion)
    
    secs = int(time.time() - start_time)
    mins = secs / 60
    secs = secs % 60
    
    
    print('Epoch: %d' %(epoch + 1), " | time in %d minutes, %d seconds" %(mins, secs))
    print(f'\tLoss: {train_loss:.4f}(train)\t|\tAcc: {train_acc * 100:.1f}%(train)')
    print(f'\tLoss: {valid_loss:.4f}(valid)\t|\tAcc: {valid_acc * 100:.1f}%(valid)')

<ipython-input-63-79b58313e02c>:11: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  x = F.softmax(self.fc3(x))


Epoch: 1  | time in 0 minutes, 4 seconds
	Loss: 0.1727(train)	|	Acc: 87.8%(train)
	Loss: 0.1466(valid)	|	Acc: 96.7%(valid)
Epoch: 2  | time in 0 minutes, 3 seconds
	Loss: 0.1461(train)	|	Acc: 96.9%(train)
	Loss: 0.1449(valid)	|	Acc: 97.3%(valid)
Epoch: 3  | time in 0 minutes, 3 seconds
	Loss: 0.1451(train)	|	Acc: 97.1%(train)
	Loss: 0.1443(valid)	|	Acc: 97.7%(valid)
Epoch: 4  | time in 0 minutes, 3 seconds
	Loss: 0.1447(train)	|	Acc: 97.3%(train)
	Loss: 0.1437(valid)	|	Acc: 98.0%(valid)
Epoch: 5  | time in 0 minutes, 3 seconds
	Loss: 0.1442(train)	|	Acc: 97.4%(train)
	Loss: 0.1448(valid)	|	Acc: 97.0%(valid)
Epoch: 6  | time in 0 minutes, 3 seconds
	Loss: 0.1441(train)	|	Acc: 97.6%(train)
	Loss: 0.1453(valid)	|	Acc: 97.0%(valid)


KeyboardInterrupt: 

In [ ]:
print('Checking the results of test dataset...')
test_loss, test_acc = test(net, dataset_test, criterion)
print(f'\tLoss: {test_loss:.4f}(test)\t|\tAcc: {test_acc * 100:.1f}%(test)')

In [ ]:
correct = 0
total = 0
with torch.no_grad():
    for i in range(tensor_x.shape[0]):
        inp = tensor_x[i]
        ground_truth = tensor_y[i]
        outputs = net(inp)
        _, predicted = torch.max(outputs.data, 0)
        total += 1
        correct += (predicted == ground_truth).sum().item()

print('Accuracy of the network on the 10000 test images: %d %%' % (
    100 * correct / total))

In [ ]:
print(tensor_x[0].shape)